In [26]:
import argparse
import copy

from transformers import BertForMaskedLM, BertTokenizer, TrainingArguments, Trainer, \
    DataCollatorForLanguageModeling, IntervalStrategy

from datasets import Dataset
import os

from data_generation_knowledge import *
from utils import *
from custom_trainer import CustomTrainer
from datasets import load_metric
import logging
from transformers import logging as tlogging
import wandb
import sys
from utils import set_seed
from transformers.integrations import WandbCallback, TensorBoardCallback
from tqdm.notebook import tqdm
from collections import Counter
from run_knowledge import *

In [27]:
set_seed(42)

run_name = 'KT_fr_bert'
epochs = 200
batch_size = 256
lr = 5e-5

source_language = ['fr']
target_language = ['en']
n_relations = 10
n_facts = 1000

In [28]:
# ~~ DATA GENERATION ~~
train, validation, test, relations, precision_k, _ = generate_knowledge_transfer(
    source_language=source_language,
    target_language=target_language,
    n_relations=n_relations,
    n_facts=n_facts,
    run_name=run_name,
    evaluate_test=True
)

In [29]:
relations

id                     en                                  de  \
690  P4032            reviewed by                       überprüft von   
775   P514       interleaves with                        verzahnt mit   
63   P3027       open period from              geöffnet von Zeitpunkt   
531  P3301           broadcast by                    ausgestrahlt von   
66   P1455          list of works                           Werkliste   
748  P1038               relative                           Verwandte   
382  P1302   primary destinations                           Hauptorte   
682   P552             handedness                          Händigkeit   
554  P4878             symbolizes                        symbolisiert   
624  P3438  vehicle normally used  normalerweise verwendetes Fahrzeug   

                             es                                fr  count  \
690                revisado por                       examiné par    507   
775             intercalada con                   s'imbrique avec     31   
63                abierto desde   début de la période d'ouverture     16   
531             transmitido por                       diffusé par   7411   
66               lista de obras                  liste des œuvres   1227   
748                    pariente                         parentèle  51652   
382        destinos principales  principales localités desservies   3923   
682                 lateralidad                    latéralisation   2256   
554                   simboliza                         symbolise     51   
624  vehículo usado normalmente   véhicule habituellement utilisé   2892   

                                              en_alias  \
690                    [examined by, peer reviewed by]   
775                                 [interbedded with]   
63     [start opening season, start of opening season]   
531  [broadcaster, TV channel, TV network, radio ch...   
66   [bibliography, catalog of works, catalogue of ...   
748  [family, family member, kinsman, relation, unc...   
382                                               None   
682                                    [dominant hand]   
554             [a symbol for, symbol for, symbolises]   
624  [drives this car, automobile used, motorcycle ...   

                                              de_alias  \
690                                               None   
775                                               None   
63                                                None   
531                          [Sender der Ausstrahlung]   
66   [Literaturverzeichnis, Bibliografie, Werkverze...   
748                         [Verwandter, Verwandt mit]   
382                                               None   
682                                               None   
554                                               None   
624  [Fahrzeug, Gefährt, Auto, Flugzeug, Fahrrad, e...   

                                              es_alias  \
690  [verificado por, evaluado por, evaluador, revi...   
775                                  [intercalado con]   
63     [inicio del periodo de apertura, abierta desde]   
531                         [transmisora, canal de tv]   
66                                      [bibliografía]   
748                   [parentela, parientes, familiar]   
382                                               None   
682                                               None   
554                                               None   
624       [vehículo normalmente usado, auto, aeronave]   

                                              fr_alias  \
690  [vérifié par, relu par, réexaminé par, passé e...   
775                                               None   
63   [période ouverte de, période d'ouverture de, p...   
531  [chaîne de télévision, chaîne télévisée, redif...   
66                  [bibliographie, liste des oeuvres]   
748  [famille, lien familial, membre de la famille,...   
382                                         

In [30]:
# LOADING
# Load mBERT model and Tokenizer
tokenizer = BertTokenizerFast.from_pretrained('bert-base-cased')
model = BertForMaskedLM.from_pretrained("bert-base-cased")

data_collator = DataCollatorForLanguageModeling(tokenizer=tokenizer, mlm_probability=0.15)
eval_data_collator = DataCollatorForLanguageModeling(tokenizer=tokenizer, mlm=False)

Some weights of the model checkpoint at bert-base-cased were not used when initializing BertForMaskedLM: ['cls.seq_relationship.bias', 'cls.seq_relationship.weight']
- This IS expected if you are initializing BertForMaskedLM from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForMaskedLM from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [31]:
train_dict = {'sample': train}
validation_list = dict_to_list(validation)
validation_dict = {'sample': validation_list}

train_ds = Dataset.from_dict(train_dict)
validation_ds = Dataset.from_dict(validation_dict)

tokenized_train = tokenize(tokenizer, train_ds)  # Train is shuffled by Huggingface
tokenized_validation = tokenize(tokenizer, validation_ds)

  0%|          | 0/10 [00:00<?, ?ba/s]

  0%|          | 0/10 [00:00<?, ?ba/s]

In [32]:
# Save Train and Test Data
train_df = pd.DataFrame(train_dict)
test_complete_df = pd.DataFrame(validation)
test_flat_df = pd.DataFrame(validation_dict)

data_dir = './output/' + run_name + '/data/'
if not os.path.exists(data_dir):
    os.makedirs(data_dir)

train_df.to_csv(data_dir + 'train_set', index=False)
test_complete_df.to_json(data_dir + 'test_set_complete')
test_flat_df.to_csv(data_dir + 'test_set', index=False)

In [33]:
training_args = TrainingArguments(
        output_dir='./output/' + run_name + '/models/',
        num_train_epochs=epochs,
        per_device_train_batch_size=batch_size,
        per_device_eval_batch_size=128,
        learning_rate=lr,
        logging_dir='./output/' + run_name + '/tb_logs/',
        logging_strategy=IntervalStrategy.STEPS,
        logging_steps=120,
        evaluation_strategy=IntervalStrategy.STEPS,
        eval_steps=120,
        save_strategy=IntervalStrategy.STEPS,
        save_steps=120,
        save_total_limit=2,
        load_best_model_at_end=True,
        metric_for_best_model='accuracy',
        run_name=run_name,
        seed=42
    )

Using the `WAND_DISABLED` environment variable is deprecated and will be removed in v5. Use the --report_to flag to control the integrations used for logging result (for instance --report_to none).


In [34]:
trainer = CustomTrainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_train,
    eval_dataset=tokenized_validation,
    tokenizer=tokenizer,
    data_collator=data_collator,
    eval_data_collator=eval_data_collator,
    compute_metrics=precision_at_one
)

In [35]:
trainer.train()

/home/laurin/anaconda3/envs/master/lib/python3.8/site-packages/transformers/optimization.py:306: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
***** Running training *****
  Num examples = 10000
  Num Epochs = 200
  Instantaneous batch size per device = 256
  Total train batch size (w. parallel, distributed & accumulation) = 512
  Gradient Accumulation steps = 1
  Total optimization steps = 4000
/home/laurin/anaconda3/envs/master/lib/python3.8/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '


Saving model checkpoint to ./output/KT_fr_bert/models/checkpoint-120
Configuration saved in ./output/KT_fr_bert/models/checkpoint-120/config.json
Model weights saved in ./output/KT_fr_bert/models/checkpoint-120/pytorch_model.bin
tokenizer config file saved in ./output/KT_fr_bert/models/checkpoint-120/tokenizer_config.json
Special tokens file saved in ./output/KT_fr_bert/models/checkpoint-120/special_tokens_map.json
/home/laurin/anaconda3/envs/master/lib/python3.8/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '
Saving model checkpoint to ./output/KT_fr_bert/models/checkpoint-240
Configuration saved in ./output/KT_fr_bert/models/checkpoint-240/config.json
Model weights saved in ./output/KT_fr_bert/models/checkpoint-240/pytorch_model.bin
tokenizer config file saved in ./output/KT_fr_bert/mode

Special tokens file saved in ./output/KT_fr_bert/models/checkpoint-1320/special_tokens_map.json
Deleting older checkpoint [output/KT_fr_bert/models/checkpoint-1080] due to args.save_total_limit
/home/laurin/anaconda3/envs/master/lib/python3.8/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '
Saving model checkpoint to ./output/KT_fr_bert/models/checkpoint-1440
Configuration saved in ./output/KT_fr_bert/models/checkpoint-1440/config.json
Model weights saved in ./output/KT_fr_bert/models/checkpoint-1440/pytorch_model.bin
tokenizer config file saved in ./output/KT_fr_bert/models/checkpoint-1440/tokenizer_config.json
Special tokens file saved in ./output/KT_fr_bert/models/checkpoint-1440/special_tokens_map.json
Deleting older checkpoint [output/KT_fr_bert/models/checkpoint-1200] due to args.save

Deleting older checkpoint [output/KT_fr_bert/models/checkpoint-2280] due to args.save_total_limit
/home/laurin/anaconda3/envs/master/lib/python3.8/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '
Saving model checkpoint to ./output/KT_fr_bert/models/checkpoint-2640
Configuration saved in ./output/KT_fr_bert/models/checkpoint-2640/config.json
Model weights saved in ./output/KT_fr_bert/models/checkpoint-2640/pytorch_model.bin
tokenizer config file saved in ./output/KT_fr_bert/models/checkpoint-2640/tokenizer_config.json
Special tokens file saved in ./output/KT_fr_bert/models/checkpoint-2640/special_tokens_map.json
Deleting older checkpoint [output/KT_fr_bert/models/checkpoint-2400] due to args.save_total_limit
/home/laurin/anaconda3/envs/master/lib/python3.8/site-packages/torch/nn/parallel/_f

/home/laurin/anaconda3/envs/master/lib/python3.8/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '
Saving model checkpoint to ./output/KT_fr_bert/models/checkpoint-3840
Configuration saved in ./output/KT_fr_bert/models/checkpoint-3840/config.json
Model weights saved in ./output/KT_fr_bert/models/checkpoint-3840/pytorch_model.bin
tokenizer config file saved in ./output/KT_fr_bert/models/checkpoint-3840/tokenizer_config.json
Special tokens file saved in ./output/KT_fr_bert/models/checkpoint-3840/special_tokens_map.json
Deleting older checkpoint [output/KT_fr_bert/models/checkpoint-3720] due to args.save_total_limit
/home/laurin/anaconda3/envs/master/lib/python3.8/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were sca

TrainOutput(global_step=4000, training_loss=1.0409972248077393, metrics={'train_runtime': 3201.2146, 'train_samples_per_second': 624.763, 'train_steps_per_second': 1.25, 'total_flos': 1.8506258784e+16, 'train_loss': 1.0409972248077393, 'epoch': 200.0})

In [37]:
trainer.evaluate(eval_dataset=tokenized_validation)

{'eval_accuracy': 0.179,
 'eval_loss': 4.68510103225708,
 'eval_runtime': 6.4358,
 'eval_samples_per_second': 1553.801,
 'eval_steps_per_second': 6.215,
 'epoch': 200.0}

In [38]:
evaluation_relation(trainer, tokenizer, relations, source_language, target_language, run_name, copy.deepcopy(test))

Relation - source: examiné par, target: reviewed by


  0%|          | 0/1 [00:00<?, ?ba/s]

/home/laurin/anaconda3/envs/master/lib/python3.8/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '


{'eval_accuracy': 0.137, 'eval_loss': 4.2195329666137695, 'eval_runtime': 1.0346, 'eval_samples_per_second': 966.551, 'eval_steps_per_second': 3.866}
Relation - source: s'imbrique avec, target: interleaves with


  0%|          | 0/1 [00:00<?, ?ba/s]

...

/home/laurin/anaconda3/envs/master/lib/python3.8/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '


{'eval_accuracy': 0.949, 'eval_loss': 0.3820028603076935, 'eval_runtime': 1.0487, 'eval_samples_per_second': 953.605, 'eval_steps_per_second': 3.814}
Relation - source: véhicule habituellement utilisé, target: vehicle normally used


  0%|          | 0/1 [00:00<?, ?ba/s]

/home/laurin/anaconda3/envs/master/lib/python3.8/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '


{'eval_accuracy': 0.022, 'eval_loss': 6.765503883361816, 'eval_runtime': 1.0687, 'eval_samples_per_second': 935.757, 'eval_steps_per_second': 3.743}


In [56]:
evaluation_alias2(trainer, tokenizer, relations, source_language, target_language, copy.deepcopy(test), 'alias')

RELATION: examiné par
-> LANGUAGE: en - TARGET: reviewed by
Number of Aliases: %i 2
ALIAS: examined by


  0%|          | 0/1 [00:00<?, ?ba/s]

/home/laurin/anaconda3/envs/master/lib/python3.8/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '


{'eval_accuracy': 0.134, 'eval_loss': 4.135285377502441, 'eval_runtime': 1.2332, 'eval_samples_per_second': 810.921, 'eval_steps_per_second': 3.244, 'epoch': 200.0}
ALIAS: peer reviewed by


  0%|          | 0/1 [00:00<?, ?ba/s]

...

/home/laurin/anaconda3/envs/master/lib/python3.8/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '


{'eval_accuracy': 0.022, 'eval_loss': 6.80311918258667, 'eval_runtime': 1.1155, 'eval_samples_per_second': 896.46, 'eval_steps_per_second': 3.586, 'epoch': 200.0}
ALIAS: trains normally used


  0%|          | 0/1 [00:00<?, ?ba/s]

/home/laurin/anaconda3/envs/master/lib/python3.8/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '


{'eval_accuracy': 0.016, 'eval_loss': 7.011819839477539, 'eval_runtime': 1.1457, 'eval_samples_per_second': 872.799, 'eval_steps_per_second': 3.491, 'epoch': 200.0}


In [57]:
evaluation_alias2(trainer, tokenizer, relations, source_language, target_language, copy.deepcopy(test), 'translate')

RELATION: examiné par
-> LANGUAGE: en - TARGET: reviewed by
Number of Translations: %i 2
ALIAS: checked by


  0%|          | 0/1 [00:00<?, ?ba/s]

/home/laurin/anaconda3/envs/master/lib/python3.8/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '


{'eval_accuracy': 0.126, 'eval_loss': 4.298323154449463, 'eval_runtime': 1.051, 'eval_samples_per_second': 951.476, 'eval_steps_per_second': 3.806, 'epoch': 200.0}
ALIAS: examined by


  0%|          | 0/1 [00:00<?, ?ba/s]

...

/home/laurin/anaconda3/envs/master/lib/python3.8/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '


{'eval_accuracy': 0.021, 'eval_loss': 6.662711143493652, 'eval_runtime': 1.141, 'eval_samples_per_second': 876.405, 'eval_steps_per_second': 3.506, 'epoch': 200.0}
ALIAS: normally used vehicle


  0%|          | 0/1 [00:00<?, ?ba/s]

/home/laurin/anaconda3/envs/master/lib/python3.8/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '


{'eval_accuracy': 0.015, 'eval_loss': 7.03277587890625, 'eval_runtime': 1.0868, 'eval_samples_per_second': 920.112, 'eval_steps_per_second': 3.68, 'epoch': 200.0}


In [58]:
evaluation_alias2(trainer, tokenizer, relations, source_language, target_language, copy.deepcopy(test), 'subword')

RELATION: examiné par
-> LANGUAGE: en - TARGET: reviewed by
Number of Words: %i 6
ALIAS: reviewed


  0%|          | 0/1 [00:00<?, ?ba/s]

/home/laurin/anaconda3/envs/master/lib/python3.8/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '


{'eval_accuracy': 0.086, 'eval_loss': 5.096198081970215, 'eval_runtime': 1.0265, 'eval_samples_per_second': 974.149, 'eval_steps_per_second': 3.897, 'epoch': 200.0}
ALIAS: checked


  0%|          | 0/1 [00:00<?, ?ba/s]

...

/home/laurin/anaconda3/envs/master/lib/python3.8/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '


{'eval_accuracy': 0.018, 'eval_loss': 6.700624942779541, 'eval_runtime': 1.0027, 'eval_samples_per_second': 997.325, 'eval_steps_per_second': 3.989, 'epoch': 200.0}
ALIAS: used


  0%|          | 0/1 [00:00<?, ?ba/s]

/home/laurin/anaconda3/envs/master/lib/python3.8/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '


{'eval_accuracy': 0.007, 'eval_loss': 7.438594818115234, 'eval_runtime': 1.2926, 'eval_samples_per_second': 773.644, 'eval_steps_per_second': 3.095, 'epoch': 200.0}


In [52]:
def evaluation_alias2(trainer, tokenizer, relations, source_language, target_language, test, test_key='relation'):
    # Create separate language Datasets for evaluation
    test_datasets = []

    # Update the precision dict for alias with test_key (alias, translation
    precision_k = defaultdict(int)
    for lang in test:
        for relation in test[lang]:
            for alias_relation in test[lang][relation][test_key]:
                for subj_rel in test[lang][relation][test_key][alias_relation]:
                    precision_k[subj_rel] = len(test[lang][relation][test_key][alias_relation][subj_rel])
    trainer.precision_dict = tokenize_dict_keys(precision_k, tokenizer)

    # Reformat test
    test = test_to_normal_alias(test, test_key)
    test_relations = flatten_remove_dict4(test, test_key)

    for language_code in test.keys():
        language_ds = Dataset.from_dict({language_code: test_relations[language_code]})
        test_datasets.append(language_ds)

    # Iterate over relations to evaluate
    for _, relation in relations.iterrows():
        for source in source_language:
            print(f'RELATION: {relation[source]}')

        # Iterate over all relations per target language
        for test_lang in target_language:
            print(f'-> LANGUAGE: {test_lang} - TARGET: {relation[test_lang]}')

            if test_key == 'alias':
                print("Number of Aliases: %i", len(test_relations[test_lang][relation[test_lang]]))
            elif test_key == 'translate':
                print("Number of Translations: %i", len(test_relations[test_lang][relation[test_lang]]))
            elif test_key == 'subword':
                print("Number of Words: %i", len(test_relations[test_lang][relation[test_lang]]))

            # Skip if no relations to evaluate
            if not test_relations[test_lang][relation[test_lang]]:
                continue

            for alias in test_relations[test_lang][relation[test_lang]]:
                print(f'ALIAS: {alias}')
                # Relation from test set dict
                relation_test = test_relations[test_lang][relation[test_lang]][alias]

                # Tokenize
                relation_test_ds = Dataset.from_dict({'sample': relation_test})
                tokenized_relation_ds = tokenize(tokenizer, relation_test_ds)

                # Evaluate
                logger.info(test_key.title() + ': ' + alias)
                print(trainer.evaluate(eval_dataset=tokenized_relation_ds))

#### Testing

In [55]:
model.to('cuda')
model.eval()

BertForMaskedLM(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(28996, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0): BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=Tr

In [43]:
train_dict['sample']

['Slovakia examiné par Kappa',
 'Engine examiné par Din',
 'Kennedy examiné par Shadows',
 'BS examiné par Innocent',
 'Terra examiné par Deputy',
 'Bavaria examiné par Walsh',
 'Guinness examiné par XVI',
 'Mass examiné par Hop',
 'Witness examiné par Merrill',
 'Milo examiné par Sicily',
 'Lille examiné par Riley',
 'Cornwall examiné par Natal',
 'Nike examiné par Edmond',
 'Elaine examiné par Mesa',
 'Wales examiné par Sheldon',
 'Hotel examiné par Anthology',
 'Wisdom examiné par Kansas',
 'Paterson examiné par Nacional',
 'Bangor examiné par Irwin',
 'Jefferson examiné par Belt',
 'Webster examiné par Austrian',
 'Fighting examiné par Franz',
 'Assessment examiné par Cardiff',
 'Rhode examiné par Ortiz',
 'Frederick examiné par Trinity',
 'Gaza examiné par Seymour',
 'Vivian examiné par Tau',
 'Honey examiné par Sage',
 'Alexander examiné par Hey',
 'Duty examiné par Clarence',
 'Superman examiné par Depot',
 'Spencer examiné par IS',
 'STS examiné par Classics',
 'Borough examiné

In [49]:
tokenizer(' examiné par ')

{'input_ids': [101, 12211, 1394, 2744, 14247, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [44]:
test

defaultdict(<function data_generation_knowledge.generate_knowledge.<locals>.<lambda>()>,
            {'en': {'reviewed by': {'relation': defaultdict(list,
                           {'Slovakia reviewed by': ['Kappa'],
                            'Engine reviewed by': ['Din'],
                            'Kennedy reviewed by': ['Shadows'],
                            'BS reviewed by': ['Innocent'],
                            'Terra reviewed by': ['Deputy'],
                            'Bavaria reviewed by': ['Walsh'],
                            'Guinness reviewed by': ['XVI'],
                            'Mass reviewed by': ['Hop'],
                            'Witness reviewed by': ['Merrill'],
                            'Milo reviewed by': ['Sicily'],
                            'Lille reviewed by': ['Riley'],
                            'Cornwall reviewed by': ['Natal'],
                            'Nike reviewed by': ['Edmond'],
                            'Elaine reviewed by': [



#### Manual Testing

In [42]:
k = 0
total = len(train_dict['sample'])
i = 0

for txt in train_dict['sample'][:10000]:
    i += 1
    
    # Add [MASK] for object
    sample = txt.rsplit(' ', 1)[0] + ' [MASK]'
    label_token = tokenizer.convert_tokens_to_ids(txt.rsplit(' ', 1)[1])
    
    encoded_input = tokenizer(sample, return_tensors='pt')
    token_logits = model(**encoded_input).logits
    
    mask_token_index = torch.where(encoded_input["input_ids"] == tokenizer.mask_token_id)[1]
    mask_token_logits = token_logits[0, mask_token_index, :]
    
    # Pick the [MASK] candidates with the highest logits
    top_1_tokens = torch.topk(mask_token_logits, 1, dim=1).indices[0].tolist()
    
    if label_token in top_1_tokens:
        k += 1

print(k/i)

0.9139


In [15]:
# Load Tokenizer and Model if not given
tokenizer = BertTokenizerFast.from_pretrained('bert-base-multilingual-cased')
model = BertForMaskedLM.from_pretrained("bert-base-multilingual-cased")

Some weights of the model checkpoint at bert-base-multilingual-cased were not used when initializing BertForMaskedLM: ['cls.seq_relationship.weight', 'cls.seq_relationship.bias']
- This IS expected if you are initializing BertForMaskedLM from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForMaskedLM from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [17]:
# Replace entity2 by [MASK]
fact = 'Harry is Tim'
word_list = fact.split()
entity2 = word_list[-1]
query = fact.replace(entity2, '') + '[MASK]'

In [23]:
# Get Top 5 Tokens
encoded_input = tokenizer(query, return_tensors='pt')
token_logits = model(**encoded_input).logits

mask_token_index = torch.where(encoded_input["input_ids"] == tokenizer.mask_token_id)[1]
mask_token_logits = token_logits[0, mask_token_index, :]

# Pick the [MASK] candidates with the highest logits
top_5_tokens = torch.topk(mask_token_logits, 5, dim=1).indices[0].tolist()

for chunk in top_5_tokens:
    if entity2 in tokenizer.decode(chunk):
        return False

SyntaxError: 'return' outside function (2948525193.py, line 13)

In [ ]:
train_dict['sample']

In [ ]:
test_dict['sample']

In [51]:
text = "Slovakia reviewed by [MASK]"
encoded_input = tokenizer(text, return_tensors='pt')
token_logits = model(**encoded_input).logits

mask_token_index = torch.where(encoded_input["input_ids"] == tokenizer.mask_token_id)[1]
mask_token_logits = token_logits[0, mask_token_index, :]

# Pick the [MASK] candidates with the highest logits
top_5_tokens = torch.topk(mask_token_logits, 5, dim=1).indices[0].tolist()

for chunk in top_5_tokens:
    print(f"\n'>>> {tokenizer.decode(chunk)}'")


'>>> Byron'

'>>> Exeter'

'>>> PM'

'>>> Atlas'

'>>> NWA'


In [45]:
for t in train_dict['sample']:
    if 'Slovakia' in t:
        print(t)

Slovakia examiné par Kappa
Slovakia s'imbrique avec Exeter
Slovakia début de la période d'ouverture Red
Slovakia diffusé par PM
Bangor diffusé par Slovakia
Rae diffusé par Slovakia
Slovakia liste des œuvres Ella
Slovakia parentèle NWA
Slovakia principales localités desservies Lindsay
Slovakia latéralisation Dictionary
Slovakia symbolise Byron
Slovakia véhicule habituellement utilisé Marvin


In [11]:
basemodel = BertForMaskedLM.from_pretrained("bert-base-multilingual-cased")

Some weights of the model checkpoint at bert-base-multilingual-cased were not used when initializing BertForMaskedLM: ['cls.seq_relationship.bias', 'cls.seq_relationship.weight']
- This IS expected if you are initializing BertForMaskedLM from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForMaskedLM from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [20]:
text = "Dresner [MASK]"
encoded_input = tokenizer(text, return_tensors='pt')
token_logits = basemodel(**encoded_input).logits

mask_token_index = torch.where(encoded_input["input_ids"] == tokenizer.mask_token_id)[1]
mask_token_logits = token_logits[0, mask_token_index, :]

# Pick the [MASK] candidates with the highest logits
top_5_tokens = torch.topk(mask_token_logits, 5, dim=1).indices[0].tolist()

for chunk in top_5_tokens:
    print(f"\n'>>> {tokenizer.decode(chunk)}'")


'>>> .'

'>>> ,'

'>>> Land'

'>>> :'

'>>> ;'
